In [1]:
import os

os.chdir("../..")
os.getcwd()

'/home/INTEXSOFT/maksim.stupakevich/work/ds_practice'

In [2]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from Levenshtein import editops
from scipy import stats
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

In [3]:
train_df = pd.read_csv("data/enzyme/train.csv", index_col="seq_id")

In [4]:
updated_df = pd.read_csv("data/enzyme/train_updates_20220929.csv", index_col="seq_id")

In [5]:
updated_df = updated_df.drop(["data_source"], axis=1).dropna()

In [6]:
train_df.update(updated_df)

In [7]:
train_df

protein_sequence   pH  \
seq_id                                                           
0       AAAAKAAALALLGEAPEVVDIWLPAGWRQPFRVFRLERKGDGVLVG...  7.0   
1       AAADGEPLHNEEERAGAGQVGRSLPQESEEQRTGSRPRRRRDLGSR...  7.0   
2       AAAFSTPRATSYRILSSAGSGSTRADAPQVRRLHTTRDLLAKDYYA...  7.0   
3       AAASGLRTAIPAQPLRHLLQPAPRPCLRPFGLLSVRAGSARRSGLL...  7.0   
4       AAATKSGPRRQSQGASVRTFTPFYFLVEPVDTLSVRGSSVILNCSA...  7.0   
...                                                   ...  ...   
31385   YYMYSGGGSALAAGGGGAGRKGDWNDIDSIKKKDLHHSRGDEKAQG...  7.0   
31386   YYNDQHRLSSYSVETAMFLSWERAIVKPGAMFKKAVIGFNCNVDLI...  7.0   
31387   YYQRTLGAELLYKISFGEMPKSAQDSAENCPSGMQFPDTAIAHANV...  7.0   
31388   YYSFSDNITTVFLSRQAIDDDHSLSLGTISDVVESENGVVAADDAR...  7.0   
31389   YYVPDEYWQSLEVAHKLTFGYGYLTWEWVQGIRSYVYPLLIAGLYK...  7.0   

                              data_source    tm  
seq_id                                           
0       doi.org/10.1038/s41592-020-0801-4  75.7  
1       doi.org/10.1038/s41592-020-0801-4  50.5  
2       doi.org/10.1038/s41592-020-0801-4  40.5  
3       doi.org/10.1038/s41592-020-0801-4  47.2  
4       doi.org/10.1038/s41592-020-0801-4  49.5  
...                                   ...   ...  
31385   doi.org/10.1038/s41592-020-0801-4  51.8  
31386   doi.org/10.1038/s41592-020-0801-4  37.2  
31387   doi.org/10.1038/s41592-020-0801-4  64.6  
31388   doi.org/10.1038/s41592-020-0801-4  50.7  
31389   doi.org/10.1038/s41592-020-0801-4  37.6  

[31390 rows x 4 columns]

In [50]:
from tqdm import tqdm

In [ ]:
def group(df):
    groups = {}
    proteins = df["protein_sequence"].unique()
    with tqdm(total=proteins.shape[0]) as pbar:
        while proteins.shape[0]:
            protein = proteins[0]
            groups[protein] = []
            for i, el in enumerate(proteins[1:]):
                similar = editops(protein, el)
                # print(similar)
                if len(similar) <= 10:
                    groups[protein].append(el)
                    proteins = np.delete(proteins, i + 1, 0)
            proteins = proteins[1:]
            pbar.update(len(groups[protein]) + 1)

    return groups

In [69]:
groups = group(train_df)

100%|███████████████████████████████████| 28981/28981 [5:11:57<00:00,  1.55it/s]


In [73]:
dict((k, v) for k, v in groups.items() if v)

{'AACFWRRTVIPKPPFRGISTTSARSTVMPAWVIDKYGKNEVLRFTQNMMLPIIHYPNEVIIKVHAASVNPIDVNMRSGYGATALNMKRDPLHMKTKGEEFPLTLGRDVSGVVMECGLDVKYFQPGDEVWAAVPPWKQGTLSEFVVVSGNEVSHKPKSLTHTQAASLPYVALTAWSAINKVGGLSDKNCKGKRALILGASGGVGTFAIQVMKAWGAHVTAVCSKDASELVRKLGADEVIDYTLGSVEEQLKSLKLFDFILDNVGGSTETWALNFLKKWSGATYVTLVTPFLLNMDRLGVADGMLQTGVTVGTKALKHLWQGVHYRWAFFMASGPYLDEIAELVDAGKIRPVIERTFPFSEVPEAFLKVERGHARGKTVVNV': ['AACFWRRTVIPKPPFRGISTTSARSTVMPAWVIDKYGKNEVLRFTQNMMLPIIHYPNEVIIKVHAASVNPIDVNMRSGYGATALNMKRDPLHMKTKGEEFPLTLGRDVSGVVMECGLDVKYFQPGDEVWAAVPPWKQGTLSEFVVVSGNEVSHKPKSLTHTQAASLPYVALTAWSAINKVGGLSDRNCKGKRALILGASGGVGTFAIQVMKAWGAHVTAVCSKDASELVRKLGADEVIDYTLGSVEEQLKSLKLFDFILDNVGGSTETWALNFLKKWSGATYVTLVTPFLLNMDRLGVADGMLQTGVTVGTKALKHLWQGVHYRWAFFMASGPYLDEIAELVDAGKIRPVIERTFPFSEVPEAFLKVERGHARGKTVVNV'],
 'AATSVFCGSSHRQLHHAVIPHGKGGRSSVSGVVATVFGATGFLGRYVVNHLGRMGSQVIIPYRCDVYDIMHLRLMGDLGQLTFLEWDARDKDSIRKAVQHSNVVINLIGREWETRNFDFEDVFVNIPRAIAQASKEAGVERFIHVSHLNASMKSSSKSLRSKAVGEKEVRSVFPEAIIIRPSDIFGREDRFLNHFANYRWFLAVPLVSLGFKTVKQPVYVADVSKGI

In [71]:
import pickle

with open("data/enzyme/train_groups_initial.pkl", "wb") as f:
    pickle.dump(groups, f)

In [77]:
groups1 = {i: [k, *v] for i, (k, v) in enumerate(groups.items()) if v}

In [80]:
groups1 = {i: v for i, (k, v) in enumerate(groups1.items())}

In [81]:
import pickle

with open("data/enzyme/train_groups.pkl", "wb") as f:
    pickle.dump(groups1, f)